# Generate Data Train and Valid Datafiles STFT
## and save them (.npy) to disk

# GTzan Artists Dataset



http://marsyasweb.appspot.com/download/data_sets/
The dataset consists of 1000 audio tracks each 30 seconds long.
It contains 10 genres, each represented by 100 tracks.
The tracks are all 22050Hz Mono 16-bit audio files in .wav format.
##### 8 May 2019
#### Alessandro L. Koerich

In [93]:
# Imports
import numpy as np
import soundfile as sf
import os, sys
import librosa
import gc


In [94]:
# Path to the 30s wavefiles sampled at 22,050 Hz with 75% overlapping
base_path = 'gtzan_3f_Win_110250_75/'

In [95]:
frame_size = 110250

In [96]:
#ONLY MODIFY THESE 2 LINES

train_folds   = [1, 2]
test_fold     = [3]

In [97]:
# Put all filenames into a list
train_filename_list = []
test_filename_list  = []

o_fold = str(test_fold[0])
f_s_folds = str(train_folds[0])+'-'+str(train_folds[1])

i  = 0
ii = 0
for ii in train_folds:

    path = base_path+"fold"+str(ii)

    for path, subdirs, files in os.walk( path ):
        for name in files:
            train_filename_list.append( os.path.join(path, name) )
            i += 1
    print("Train files processed: "+"fold"+str(ii)+" "+str(i) )
    
j  = 0 
ii = 0
for ii in test_fold:

    path = base_path+"fold"+str(ii)

    for path, subdirs, files in os.walk( path ):
        for name in files:
            test_filename_list.append( os.path.join(path, name) )
            j += 1
    print("Test files processed: "+"fold"+str(ii)+" "+str(j) )
    

Train files processed: fold1 7138
Train files processed: fold2 14051
Test files processed: fold3 6929


In [98]:
train_filename_list

['gtzan_3f_Win_110250_75/fold1/metal/689_20.wav',
 'gtzan_3f_Win_110250_75/fold1/metal/677_6.wav',
 'gtzan_3f_Win_110250_75/fold1/metal/678_13.wav',
 'gtzan_3f_Win_110250_75/fold1/metal/692_5.wav',
 'gtzan_3f_Win_110250_75/fold1/metal/688_7.wav',
 'gtzan_3f_Win_110250_75/fold1/metal/686_13.wav',
 'gtzan_3f_Win_110250_75/fold1/metal/683_5.wav',
 'gtzan_3f_Win_110250_75/fold1/metal/685_18.wav',
 'gtzan_3f_Win_110250_75/fold1/metal/661_17.wav',
 'gtzan_3f_Win_110250_75/fold1/metal/691_13.wav',
 'gtzan_3f_Win_110250_75/fold1/metal/688_12.wav',
 'gtzan_3f_Win_110250_75/fold1/metal/665_13.wav',
 'gtzan_3f_Win_110250_75/fold1/metal/664_15.wav',
 'gtzan_3f_Win_110250_75/fold1/metal/693_14.wav',
 'gtzan_3f_Win_110250_75/fold1/metal/690_15.wav',
 'gtzan_3f_Win_110250_75/fold1/metal/668_10.wav',
 'gtzan_3f_Win_110250_75/fold1/metal/681_4.wav',
 'gtzan_3f_Win_110250_75/fold1/metal/679_1.wav',
 'gtzan_3f_Win_110250_75/fold1/metal/664_3.wav',
 'gtzan_3f_Win_110250_75/fold1/metal/676_11.wav',
 'gtzan

In [99]:
import random
random.shuffle(train_filename_list,random.random)

In [100]:
train_filename_list

['gtzan_3f_Win_110250_75/fold1/pop/697_14.wav',
 'gtzan_3f_Win_110250_75/fold1/rock/861_1.wav',
 'gtzan_3f_Win_110250_75/fold2/disco/540_5.wav',
 'gtzan_3f_Win_110250_75/fold1/classical/824_20.wav',
 'gtzan_3f_Win_110250_75/fold2/hiphop/516_14.wav',
 'gtzan_3f_Win_110250_75/fold1/disco/916_19.wav',
 'gtzan_3f_Win_110250_75/fold1/disco/901_2.wav',
 'gtzan_3f_Win_110250_75/fold2/country/454_19.wav',
 'gtzan_3f_Win_110250_75/fold2/country/461_3.wav',
 'gtzan_3f_Win_110250_75/fold2/jazz/625_5.wav',
 'gtzan_3f_Win_110250_75/fold2/pop/380_1.wav',
 'gtzan_3f_Win_110250_75/fold2/blues/422_21.wav',
 'gtzan_3f_Win_110250_75/fold1/classical/798_21.wav',
 'gtzan_3f_Win_110250_75/fold2/reggae/484_21.wav',
 'gtzan_3f_Win_110250_75/fold1/country/774_16.wav',
 'gtzan_3f_Win_110250_75/fold1/country/780_20.wav',
 'gtzan_3f_Win_110250_75/fold1/metal/689_18.wav',
 'gtzan_3f_Win_110250_75/fold2/hiphop/527_12.wav',
 'gtzan_3f_Win_110250_75/fold2/pop/375_18.wav',
 'gtzan_3f_Win_110250_75/fold1/country/773_19

In [101]:
# Get size of Spectrogram

file_wave, sr = librosa.load("gtzan_3f_Win_110250_75/fold1/rock/864_3.wav") # load original audio, sr default is 22050
    
original_stft = librosa.stft(file_wave, n_fft=512, hop_length=256)
real_part = original_stft.real
imag_part = original_stft.imag

#Eliminate negative values
coef = max(np.abs(real_part.max()), np.abs(real_part.min()))
real_part += coef

dB_spec = librosa.amplitude_to_db(real_part)
    
dB_spec_shape = dB_spec.shape
print(dB_spec_shape)


(257, 431)


In [102]:
# Create a big matrix to accomodate train files
spchnumber_train = i
spchmatrix_train = np.ones((spchnumber_train, dB_spec_shape[0], dB_spec_shape[1]), dtype=float)
print(spchmatrix_train.shape)

(14051, 257, 431)


In [103]:
# Create a big matrix to accomodate test files
spchnumber_test = j
spchmatrix_test = np.ones((spchnumber_test, dB_spec_shape[0], dB_spec_shape[1]), dtype=float)
print(spchmatrix_test.shape)

(6929, 257, 431)


In [104]:
# Create matrix for coefs test files
coefmatrix = np.ones((spchnumber_test), dtype=float)
print(coefmatrix.shape)

(6929,)


In [105]:
# Create matrix for phases test files
phasesmatrix = np.ones((spchnumber_test, dB_spec_shape[0], dB_spec_shape[1]), dtype=float)
print(phasesmatrix.shape)

(6929, 257, 431)


In [106]:
# Fill the matrix with train data 
i = 0

for filepath in train_filename_list:
    
    file_wave, sr = librosa.load(filepath) # load original audio, sr default is 22050
    original_stft = librosa.stft(file_wave, n_fft=512, hop_length=256)
    shape_stft = original_stft.shape

    # Split into real and imaginary parts
    real_part = original_stft.real
    imag_part = original_stft.imag

    coef = max(np.abs(real_part.max()), np.abs(real_part.min()))
    
    real_part = real_part+coef #Add coef to eliminate negative values
    dB_spec = librosa.amplitude_to_db(real_part)

    spchmatrix_train[i,:] = dB_spec
    
    i += 1
    if (i%1000 == 0.000):
        print("Files read: "+str(i) )

print("Train matrix filled")

Files read: 1000
Files read: 2000
Files read: 3000
Files read: 4000
Files read: 5000
Files read: 6000
Files read: 7000
Files read: 8000
Files read: 9000
Files read: 10000
Files read: 11000
Files read: 12000
Files read: 13000
Files read: 14000
Train matrix filled


In [107]:
## Save data files (input arrays) to disk (.npy files)
spchmatrix_train_shape = spchmatrix_train.shape
#half = spchmatrix_train_shape[0]//2
np.save( "folds_stft/2_GTzan_Xs_train_fold"+f_s_folds+"_110250_75_frozen_stft.npy", spchmatrix_train) #[:half])
#np.save( "folds_stft/2_GTzan_Xs_train_fold"+f_s_folds+"_110250_75_frozen_stft_part1.npy", spchmatrix_train) #[:half])
#spchmatrix_train = None
#gc.collect()

In [108]:
#np.save( "folds_stft/2_GTzan_Xs_train_fold"+f_s_folds+"_110250_75_frozen_stft_part2.npy", spchmatrix_train[half:])

In [109]:
# Fill the matrix with test data 
j = 0

for filepath in test_filename_list:
    
    file_wave, sr = librosa.load(filepath) # load original audio, sr default is 22050
    original_stft = librosa.stft(file_wave, n_fft=512, hop_length=256)
    shape_stft = original_stft.shape

    # Split into real and imaginary parts
    real_part = original_stft.real
    imag_part = original_stft.imag
    print(imag_part.shape)
    print()
    print(imag_part)
    coef = max(np.abs(real_part.max()), np.abs(real_part.min()))
    
    real_part = real_part+coef #Add coef to eliminate negative values
    dB_spec = librosa.amplitude_to_db(real_part)

    spchmatrix_test[j,:] = dB_spec
    coefmatrix[j] = coef
    phasesmatrix[j] = imag_part

    j += 1
    if (j%100 == 0.000):
        print("Files read: "+str(j) )

print("Data matrix filled")

(257, 431)

[[ 0.0000000e+00  0.0000000e+00  0.0000000e+00 ...  0.0000000e+00
   0.0000000e+00  0.0000000e+00]
 [-4.6837534e-16  1.1773235e-02 -5.6374078e+00 ... -1.0008270e+01
  -6.1947989e+00  3.4356945e+00]
 [ 2.0424158e-15  9.8976707e+00 -3.8906994e-01 ...  6.7122922e+00
   3.6207848e+00  2.5437685e+01]
 ...
 [ 1.7803019e-16 -2.2371786e-04 -3.8673395e-05 ...  6.1875246e-05
   1.6345712e-05 -3.0069198e-02]
 [ 6.2103100e-16  1.7627007e-04 -3.7649450e-05 ...  8.6722448e-06
  -8.0070837e-05 -3.1175891e-02]
 [ 0.0000000e+00  0.0000000e+00  0.0000000e+00 ...  0.0000000e+00
   0.0000000e+00  0.0000000e+00]]
(257, 431)

[[ 0.0000000e+00  0.0000000e+00  0.0000000e+00 ...  0.0000000e+00
   0.0000000e+00  0.0000000e+00]
 [ 4.0939474e-16 -5.4369245e+00  3.3221323e+00 ... -1.3086249e+00
   6.2244577e+00 -5.7839508e+00]
 [-5.3364849e-16  5.1993928e+00 -4.9359469e+00 ... -2.0466614e+00
  -5.3598347e+00  5.3879838e+00]
 ...
 [ 3.4048140e-17 -2.5316785e-05  1.5406718e-05 ... -3.1497068e-05
   1.215

(257, 431)

[[ 0.0000000e+00  0.0000000e+00  0.0000000e+00 ...  0.0000000e+00
   0.0000000e+00  0.0000000e+00]
 [ 2.3505503e-15 -7.1577797e+00  6.1102576e+00 ... -6.6023827e+00
  -4.5420501e-01  6.7354970e+00]
 [-2.5511319e-15 -2.0520891e+01  1.1819110e+01 ...  2.7567217e-01
  -1.1173759e+00  1.2584365e+01]
 ...
 [ 1.0864125e-16 -4.0784762e-05  1.8585622e-05 ... -8.4594321e-06
  -4.8364353e-05 -2.9686657e-03]
 [ 3.1398495e-16 -3.7528807e-05  7.3983829e-05 ... -2.1624317e-05
  -7.2842403e-07 -3.0168297e-03]
 [ 0.0000000e+00  0.0000000e+00  0.0000000e+00 ...  0.0000000e+00
   0.0000000e+00  0.0000000e+00]]
(257, 431)

[[ 0.00000000e+00  0.00000000e+00  0.00000000e+00 ...  0.00000000e+00
   0.00000000e+00  0.00000000e+00]
 [ 1.17961196e-15 -4.26138783e+00 -7.22592926e+00 ...  5.77776299e+01
  -2.15662403e+01 -1.20534420e+01]
 [ 2.20360942e-16  1.03337994e+01  8.27288437e+00 ... -6.00395775e+01
   1.40963593e+01  1.21944208e+01]
 ...
 [-1.09338646e-16 -5.06232682e-05  2.16450644e-04 ... -2

(257, 431)

[[ 0.0000000e+00  0.0000000e+00  0.0000000e+00 ...  0.0000000e+00
   0.0000000e+00  0.0000000e+00]
 [-4.8138576e-17 -1.3495852e+00  1.0519938e+00 ...  2.1259537e+00
   1.0679214e-02 -2.6772838e+00]
 [ 3.2488642e-16  1.5788878e+00 -2.4009359e+00 ... -4.0325985e+00
   1.0466282e+00  1.2609541e+00]
 ...
 [-1.2365850e-16  4.5634744e-05 -2.1192494e-05 ... -7.9437719e-05
  -3.3224416e-05  3.3209906e-03]
 [-1.2533377e-16 -8.5422063e-05  6.2861713e-05 ...  8.4908585e-05
  -5.4051055e-05  3.1105310e-03]
 [ 0.0000000e+00  0.0000000e+00  0.0000000e+00 ...  0.0000000e+00
   0.0000000e+00  0.0000000e+00]]
(257, 431)

[[ 0.0000000e+00  0.0000000e+00  0.0000000e+00 ...  0.0000000e+00
   0.0000000e+00  0.0000000e+00]
 [-2.2204460e-16  8.2478638e+00 -7.8096299e+00 ...  1.2717452e+01
   1.7921616e+01 -1.9450048e+01]
 [-2.0955460e-15 -6.2260261e+00  7.1522288e+00 ... -1.0796274e+01
  -1.6071507e+01  1.9041447e+01]
 ...
 [-1.6653345e-16 -1.0835920e-04  3.4003631e-05 ... -3.6719404e-05
   1.231

(257, 431)

[[ 0.0000000e+00  0.0000000e+00  0.0000000e+00 ...  0.0000000e+00
   0.0000000e+00  0.0000000e+00]
 [-8.3266727e-17 -9.8123159e+00  1.2826908e+01 ...  1.9248414e-01
  -3.9911802e+00 -3.0722165e+00]
 [ 1.8757803e-15  1.0265925e+01 -8.6175146e+00 ...  7.0673251e+00
   2.1205609e+00  7.5453482e+00]
 ...
 [ 1.1598867e-17 -1.1402872e-05 -7.9704150e-05 ...  4.2966683e-05
  -8.8412044e-06 -3.6975953e-03]
 [ 2.7755576e-17  3.7953534e-05  1.1284502e-04 ...  3.6447480e-05
  -2.8869626e-05 -3.6439530e-03]
 [ 0.0000000e+00  0.0000000e+00  0.0000000e+00 ...  0.0000000e+00
   0.0000000e+00  0.0000000e+00]]
(257, 431)

[[ 0.00000000e+00  0.00000000e+00  0.00000000e+00 ...  0.00000000e+00
   0.00000000e+00  0.00000000e+00]
 [-1.19348975e-15  6.12803078e+00  2.03269844e+01 ... -3.08697224e-01
  -4.88337487e-01 -6.96817255e+00]
 [-2.56245942e-16 -9.17028141e+00 -1.77054138e+01 ...  1.62507272e+00
   2.28271818e+00  7.95551300e+00]
 ...
 [-1.60087692e-16 -2.24931482e-05  1.16324249e-04 ... -2

(257, 431)

[[ 0.0000000e+00  0.0000000e+00  0.0000000e+00 ...  0.0000000e+00
   0.0000000e+00  0.0000000e+00]
 [-3.2526065e-18  3.9104906e-01 -1.7695260e+00 ... -9.4398254e-01
  -6.0132533e-01  7.6647818e-01]
 [-5.1030633e-16  3.2097203e-01  3.3239772e+00 ...  1.0887524e+00
   4.6907932e-01 -2.5513214e-01]
 ...
 [ 1.8417831e-16 -1.8273082e-05 -6.9579364e-05 ... -1.4158344e-04
   3.7108737e-05  2.3869299e-03]
 [-7.7412035e-17  3.5548610e-06  6.4932101e-05 ...  1.2821524e-04
  -1.9797013e-05  2.6703067e-03]
 [ 0.0000000e+00  0.0000000e+00  0.0000000e+00 ...  0.0000000e+00
   0.0000000e+00  0.0000000e+00]]
(257, 431)

[[ 0.0000000e+00  0.0000000e+00  0.0000000e+00 ...  0.0000000e+00
   0.0000000e+00  0.0000000e+00]
 [-1.1102230e-15  5.6052022e+00  1.1766620e+01 ...  1.0591584e+00
  -9.3911190e+00  1.2039833e+01]
 [ 1.9520061e-15 -3.7770281e+00 -1.4113110e+01 ... -5.1069846e+00
   1.5981918e+01 -9.3805561e+00]
 ...
 [-2.8667145e-16  2.5352947e-05 -5.7143236e-05 ... -1.3169843e-05
  -4.436

...

(257, 431)

[[ 0.0000000e+00  0.0000000e+00  0.0000000e+00 ...  0.0000000e+00
   0.0000000e+00  0.0000000e+00]
 [ 1.0833348e-15 -2.1197286e+00 -2.3411903e-01 ... -1.7502103e+00
   6.3769917e+00 -5.3700976e+00]
 [ 1.1790167e-15  6.8538465e+00 -4.9033070e+00 ... -1.8947608e+00
   1.7758191e+00 -1.6197454e+00]
 ...
 [ 4.5856225e-16  1.8283309e-03  4.9176752e-03 ... -2.5652122e-02
  -5.8812630e-01 -4.2574752e-02]
 [-8.4134089e-17 -6.2867315e-03 -4.9021933e-03 ...  7.7486396e-02
   2.9602653e-01 -3.2498759e-01]
 [ 0.0000000e+00  0.0000000e+00  0.0000000e+00 ...  0.0000000e+00
   0.0000000e+00  0.0000000e+00]]
(257, 431)

[[ 0.00000000e+00  0.00000000e+00  0.00000000e+00 ...  0.00000000e+00
   0.00000000e+00  0.00000000e+00]
 [ 6.21031004e-16 -6.22910440e-01 -5.76362908e-01 ...  1.65670264e+00
  -4.45102900e-01 -1.07834041e-01]
 [ 2.41670755e-16 -1.92891145e+00 -2.47854635e-01 ...  2.19794321e+00
   5.54113425e-02  2.83323145e+00]
 ...
 [ 1.46907303e-16  6.05328496e-05 -1.17295585e-05 ...  1

(257, 431)

[[ 0.0000000e+00  0.0000000e+00  0.0000000e+00 ...  0.0000000e+00
   0.0000000e+00  0.0000000e+00]
 [ 8.2746310e-16  2.7342246e+00 -4.3937497e+00 ...  2.8430967e+00
  -1.0683945e+00 -3.8054686e+00]
 [-3.2537955e-16 -2.8328140e+00  3.5417061e+00 ... -3.7885568e+00
   1.8826221e+00  8.7225370e+00]
 ...
 [-5.9729058e-17  7.4895848e-05 -1.6143998e-05 ... -1.2625007e-04
  -8.1075323e-06 -2.5046926e-03]
 [-5.4296845e-16 -1.2238108e-04  5.0931503e-05 ...  1.9877208e-04
  -3.9147744e-05 -2.5841317e-03]
 [ 0.0000000e+00  0.0000000e+00  0.0000000e+00 ...  0.0000000e+00
   0.0000000e+00  0.0000000e+00]]
(257, 431)

[[ 0.00000000e+00  0.00000000e+00  0.00000000e+00 ...  0.00000000e+00
   0.00000000e+00  0.00000000e+00]
 [ 5.34294831e-16  8.54141474e-01 -1.55392909e+00 ... -3.02150220e-01
  -7.01621175e-03 -3.85907149e+00]
 [ 4.07013678e-16 -4.29051447e+00 -1.41698873e+00 ...  1.92538941e+00
   2.67476678e+00  3.46234298e+00]
 ...
 [-1.43335723e-16  3.13513083e-05 -1.50607084e-04 ...  3

(257, 431)

[[ 0.0000000e+00  0.0000000e+00  0.0000000e+00 ...  0.0000000e+00
   0.0000000e+00  0.0000000e+00]
 [ 5.1347815e-16 -9.2835226e+00  8.8791904e+00 ... -6.9932038e-01
  -2.1874237e+00 -1.9970522e+00]
 [ 2.0165321e-16  1.0424963e+01 -9.4730806e+00 ...  1.0386105e+00
   4.7787242e+00  5.3029222e+00]
 ...
 [ 5.1999173e-16  3.5891237e-05  6.7765075e-05 ... -7.3614734e-05
   1.1454908e-04 -6.1642881e-03]
 [-2.3592239e-16 -7.0147231e-05 -3.0430514e-05 ...  5.0431743e-05
  -7.1450799e-05 -6.1513879e-03]
 [ 0.0000000e+00  0.0000000e+00  0.0000000e+00 ...  0.0000000e+00
   0.0000000e+00  0.0000000e+00]]
(257, 431)

[[ 0.0000000e+00  0.0000000e+00  0.0000000e+00 ...  0.0000000e+00
   0.0000000e+00  0.0000000e+00]
 [ 8.9164787e-16 -1.3513595e+01  1.3046125e+01 ... -1.1596819e+01
   5.6475382e+00 -5.8695731e+00]
 [ 2.5446016e-16  1.1629257e+01 -2.8006618e+00 ...  1.1477673e+01
  -2.4831643e+00 -3.6784780e+00]
 ...
 [-1.4343786e-16  1.3410961e-03  8.3101280e-03 ...  9.8107234e-02
  -4.048

(257, 431)

[[ 0.00000000e+00  0.00000000e+00  0.00000000e+00 ...  0.00000000e+00
   0.00000000e+00  0.00000000e+00]
 [-6.17561557e-16  3.18089676e+00 -3.87881351e+00 ... -1.46618261e+01
   2.36743045e+00  1.12674990e+01]
 [ 6.87766772e-16 -6.47924519e+00  6.75927067e+00 ...  1.88239613e+01
  -6.10220242e+00 -1.46353521e+01]
 ...
 [ 5.12254094e-17  3.74047682e-02  3.04310955e-02 ...  2.38951102e-01
  -7.82195255e-02 -4.29198071e-02]
 [-1.87350135e-16 -2.87562851e-02 -6.04882464e-03 ... -1.49295419e-01
   1.12137355e-01  2.10719407e-02]
 [ 0.00000000e+00  0.00000000e+00  0.00000000e+00 ...  0.00000000e+00
   0.00000000e+00  0.00000000e+00]]
(257, 431)

[[ 0.0000000e+00  0.0000000e+00  0.0000000e+00 ...  0.0000000e+00
   0.0000000e+00  0.0000000e+00]
 [-2.8796410e-16 -5.0456047e-01 -1.0421178e+00 ... -1.6636618e+00
  -6.3939428e+00 -4.5386715e+00]
 [-4.7699787e-16  1.1185650e+00  5.3457469e-01 ...  2.9085190e+00
   1.0406553e+01  4.4400902e+00]
 ...
 [-1.6831924e-16 -3.3653148e-05  7.184

(257, 431)

[[ 0.0000000e+00  0.0000000e+00  0.0000000e+00 ...  0.0000000e+00
   0.0000000e+00  0.0000000e+00]
 [ 3.2959746e-16  2.7192252e+00  2.3267770e+00 ...  1.6685998e-01
   1.9891491e+00 -2.6404831e+00]
 [ 1.1697493e-16 -2.7255716e+00 -1.7119048e+00 ... -2.0615418e+00
  -4.0447788e+00  7.0796051e+00]
 ...
 [ 3.5486985e-16 -1.7089910e-04  1.0404945e-04 ...  1.0389830e-04
  -3.2307944e-05  3.0033628e-04]
 [-6.0021432e-16  1.7163741e-04 -1.2306505e-04 ... -1.4238113e-04
   5.9274138e-05  1.9516384e-04]
 [ 0.0000000e+00  0.0000000e+00  0.0000000e+00 ...  0.0000000e+00
   0.0000000e+00  0.0000000e+00]]
(257, 431)

[[ 0.0000000e+00  0.0000000e+00  0.0000000e+00 ...  0.0000000e+00
   0.0000000e+00  0.0000000e+00]
 [ 4.3715032e-16  4.7583632e+00 -8.5612106e+00 ... -1.7847515e+00
  -4.5244268e-01  7.7550277e-02]
 [-1.1107672e-15 -4.0707393e+00  6.6558800e+00 ...  3.4195487e+00
   4.8087429e-02  9.4875908e-01]
 ...
 [ 1.9483322e-16 -1.1703937e-04 -1.8105186e-05 ... -2.3291637e-05
  -1.369

In [110]:
## Save data files (input arrays) to disk (.npy files)
spchmatrix_test_shape = spchmatrix_test.shape
np.save( "folds_stft/2_GTzan_Xs_test_fold"+o_fold+"_110250_75_frozen_stft.npy", spchmatrix_test)
spchmatrix_test = None
gc.collect()

382

In [111]:
## Save phases and coefs
np.save( "folds_stft/2_GTzan_phase_test_fold"+o_fold+"_110250_75_frozen_stft.npy", phasesmatrix)

#phasesmatrix = None
#coefmatrix = None
#gc.collect()

In [112]:
np.save( "folds_stft/2_GTzan_coefs_test_fold"+o_fold+"_110250_75_frozen_stft.npy", coefmatrix)

In [113]:
#Verify shapes

print(spchmatrix_train_shape)
print(spchmatrix_test_shape)

(14051, 257, 431)
(6929, 257, 431)


## Prepare the correspoing labels

In [114]:
# Dataset Parameters
nb_classes = 10
frame_size = 110250

In [115]:
# Create a vector for labels
label_train = np.ones((spchnumber_train,), dtype=int)
label_test  = np.ones((spchnumber_test,), dtype=int)

In [116]:
# Let's read each genre from the filename in our list and take the first four characters of the genre directory


choices = {'blues': 0, 'classical': 1, 'country': 2, 'disco': 3, 'hiphop': 4, 'jazz': 5,
           'metal': 6, 'pop': 7, 'reggae': 8, 'rock': 9}

i = 0
for file_name in train_filename_list:
    # Take the first four characters of the file
    class_id = file_name[20:].split('/')[2]
    
    print(class_id, ' --- ', file_name)
    # Replace the (genre?) 4-character string by a number according to "choices"
    label_train[i] = choices.get( class_id, 99 )
    i += 1

pop  ---  gtzan_3f_Win_110250_75/fold1/pop/697_14.wav
rock  ---  gtzan_3f_Win_110250_75/fold1/rock/861_1.wav
disco  ---  gtzan_3f_Win_110250_75/fold2/disco/540_5.wav
classical  ---  gtzan_3f_Win_110250_75/fold1/classical/824_20.wav
hiphop  ---  gtzan_3f_Win_110250_75/fold2/hiphop/516_14.wav
disco  ---  gtzan_3f_Win_110250_75/fold1/disco/916_19.wav
disco  ---  gtzan_3f_Win_110250_75/fold1/disco/901_2.wav
country  ---  gtzan_3f_Win_110250_75/fold2/country/454_19.wav
country  ---  gtzan_3f_Win_110250_75/fold2/country/461_3.wav
jazz  ---  gtzan_3f_Win_110250_75/fold2/jazz/625_5.wav
pop  ---  gtzan_3f_Win_110250_75/fold2/pop/380_1.wav
blues  ---  gtzan_3f_Win_110250_75/fold2/blues/422_21.wav
classical  ---  gtzan_3f_Win_110250_75/fold1/classical/798_21.wav
reggae  ---  gtzan_3f_Win_110250_75/fold2/reggae/484_21.wav
country  ---  gtzan_3f_Win_110250_75/fold1/country/774_16.wav
country  ---  gtzan_3f_Win_110250_75/fold1/country/780_20.wav
metal  ---  gtzan_3f_Win_110250_75/fold1/metal/689_18.

jazz  ---  gtzan_3f_Win_110250_75/fold2/jazz/610_2.wav
reggae  ---  gtzan_3f_Win_110250_75/fold1/reggae/965_18.wav
blues  ---  gtzan_3f_Win_110250_75/fold2/blues/403_16.wav
blues  ---  gtzan_3f_Win_110250_75/fold2/blues/427_10.wav
metal  ---  gtzan_3f_Win_110250_75/fold2/metal/638_1.wav
hiphop  ---  gtzan_3f_Win_110250_75/fold2/hiphop/505_13.wav
classical  ---  gtzan_3f_Win_110250_75/fold2/classical/590_17.wav
hiphop  ---  gtzan_3f_Win_110250_75/fold1/hiphop/973_21.wav
jazz  ---  gtzan_3f_Win_110250_75/fold2/jazz/599_2.wav
rock  ---  gtzan_3f_Win_110250_75/fold1/rock/834_3.wav
hiphop  ---  gtzan_3f_Win_110250_75/fold2/hiphop/500_1.wav
classical  ---  gtzan_3f_Win_110250_75/fold1/classical/821_4.wav
jazz  ---  gtzan_3f_Win_110250_75/fold2/jazz/625_1.wav
classical  ---  gtzan_3f_Win_110250_75/fold1/classical/817_8.wav
classical  ---  gtzan_3f_Win_110250_75/fold2/classical/562_3.wav
classical  ---  gtzan_3f_Win_110250_75/fold1/classical/817_19.wav
hiphop  ---  gtzan_3f_Win_110250_75/fold2

pop  ---  gtzan_3f_Win_110250_75/fold2/pop/383_13.wav
pop  ---  gtzan_3f_Win_110250_75/fold2/pop/377_19.wav
rock  ---  gtzan_3f_Win_110250_75/fold1/rock/852_5.wav
rock  ---  gtzan_3f_Win_110250_75/fold2/rock/339_12.wav
jazz  ---  gtzan_3f_Win_110250_75/fold1/jazz/762_14.wav
classical  ---  gtzan_3f_Win_110250_75/fold1/classical/814_15.wav
rock  ---  gtzan_3f_Win_110250_75/fold2/rock/339_14.wav
pop  ---  gtzan_3f_Win_110250_75/fold1/pop/721_21.wav
hiphop  ---  gtzan_3f_Win_110250_75/fold2/hiphop/523_12.wav
country  ---  gtzan_3f_Win_110250_75/fold1/country/777_18.wav
blues  ---  gtzan_3f_Win_110250_75/fold2/blues/425_1.wav
pop  ---  gtzan_3f_Win_110250_75/fold2/pop/373_10.wav
blues  ---  gtzan_3f_Win_110250_75/fold1/blues/887_19.wav
pop  ---  gtzan_3f_Win_110250_75/fold2/pop/372_3.wav
hiphop  ---  gtzan_3f_Win_110250_75/fold2/hiphop/513_20.wav
metal  ---  gtzan_3f_Win_110250_75/fold2/metal/651_14.wav
country  ---  gtzan_3f_Win_110250_75/fold1/country/768_10.wav
disco  ---  gtzan_3f_Win_

country  ---  gtzan_3f_Win_110250_75/fold1/country/786_7.wav
reggae  ---  gtzan_3f_Win_110250_75/fold2/reggae/483_2.wav
jazz  ---  gtzan_3f_Win_110250_75/fold1/jazz/749_1.wav
country  ---  gtzan_3f_Win_110250_75/fold1/country/773_8.wav
rock  ---  gtzan_3f_Win_110250_75/fold1/rock/864_13.wav
metal  ---  gtzan_3f_Win_110250_75/fold1/metal/671_1.wav
disco  ---  gtzan_3f_Win_110250_75/fold1/disco/909_18.wav
jazz  ---  gtzan_3f_Win_110250_75/fold1/jazz/734_10.wav
pop  ---  gtzan_3f_Win_110250_75/fold1/pop/702_14.wav
classical  ---  gtzan_3f_Win_110250_75/fold1/classical/823_10.wav
hiphop  ---  gtzan_3f_Win_110250_75/fold1/hiphop/992_3.wav
country  ---  gtzan_3f_Win_110250_75/fold2/country/461_8.wav
reggae  ---  gtzan_3f_Win_110250_75/fold2/reggae/494_2.wav
rock  ---  gtzan_3f_Win_110250_75/fold2/rock/351_9.wav
disco  ---  gtzan_3f_Win_110250_75/fold1/disco/913_4.wav
jazz  ---  gtzan_3f_Win_110250_75/fold1/jazz/748_16.wav
blues  ---  gtzan_3f_Win_110250_75/fold1/blues/883_7.wav
country  --- 

metal  ---  gtzan_3f_Win_110250_75/fold1/metal/670_11.wav
pop  ---  gtzan_3f_Win_110250_75/fold1/pop/701_5.wav
jazz  ---  gtzan_3f_Win_110250_75/fold2/jazz/617_1.wav
pop  ---  gtzan_3f_Win_110250_75/fold1/pop/723_10.wav
country  ---  gtzan_3f_Win_110250_75/fold2/country/442_15.wav
disco  ---  gtzan_3f_Win_110250_75/fold1/disco/901_14.wav
reggae  ---  gtzan_3f_Win_110250_75/fold2/reggae/481_11.wav
country  ---  gtzan_3f_Win_110250_75/fold2/country/440_11.wav
metal  ---  gtzan_3f_Win_110250_75/fold1/metal/669_10.wav
blues  ---  gtzan_3f_Win_110250_75/fold2/blues/399_21.wav
hiphop  ---  gtzan_3f_Win_110250_75/fold1/hiphop/978_5.wav
country  ---  gtzan_3f_Win_110250_75/fold1/country/783_8.wav
reggae  ---  gtzan_3f_Win_110250_75/fold2/reggae/482_8.wav
country  ---  gtzan_3f_Win_110250_75/fold1/country/781_17.wav
country  ---  gtzan_3f_Win_110250_75/fold1/country/779_12.wav
metal  ---  gtzan_3f_Win_110250_75/fold1/metal/678_14.wav
classical  ---  gtzan_3f_Win_110250_75/fold2/classical/581_18

...

pop  ---  gtzan_3f_Win_110250_75/fold2/pop/369_2.wav
classical  ---  gtzan_3f_Win_110250_75/fold1/classical/802_1.wav
hiphop  ---  gtzan_3f_Win_110250_75/fold2/hiphop/499_21.wav
hiphop  ---  gtzan_3f_Win_110250_75/fold1/hiphop/993_17.wav
disco  ---  gtzan_3f_Win_110250_75/fold1/disco/904_1.wav
disco  ---  gtzan_3f_Win_110250_75/fold1/disco/908_9.wav
blues  ---  gtzan_3f_Win_110250_75/fold1/blues/870_2.wav
rock  ---  gtzan_3f_Win_110250_75/fold2/rock/338_5.wav
reggae  ---  gtzan_3f_Win_110250_75/fold2/reggae/476_11.wav
hiphop  ---  gtzan_3f_Win_110250_75/fold1/hiphop/972_18.wav
hiphop  ---  gtzan_3f_Win_110250_75/fold2/hiphop/506_10.wav
blues  ---  gtzan_3f_Win_110250_75/fold2/blues/411_17.wav
classical  ---  gtzan_3f_Win_110250_75/fold1/classical/803_11.wav
rock  ---  gtzan_3f_Win_110250_75/fold1/rock/833_12.wav
rock  ---  gtzan_3f_Win_110250_75/fold1/rock/834_16.wav
classical  ---  gtzan_3f_Win_110250_75/fold2/classical/589_7.wav
pop  ---  gtzan_3f_Win_110250_75/fold2/pop/386_3.wav
re

classical  ---  gtzan_3f_Win_110250_75/fold1/classical/816_21.wav
hiphop  ---  gtzan_3f_Win_110250_75/fold2/hiphop/508_7.wav
pop  ---  gtzan_3f_Win_110250_75/fold2/pop/384_16.wav
pop  ---  gtzan_3f_Win_110250_75/fold2/pop/379_7.wav
metal  ---  gtzan_3f_Win_110250_75/fold2/metal/649_4.wav
country  ---  gtzan_3f_Win_110250_75/fold2/country/433_10.wav
pop  ---  gtzan_3f_Win_110250_75/fold2/pop/387_3.wav
pop  ---  gtzan_3f_Win_110250_75/fold2/pop/389_3.wav
disco  ---  gtzan_3f_Win_110250_75/fold2/disco/547_8.wav
classical  ---  gtzan_3f_Win_110250_75/fold2/classical/588_19.wav
blues  ---  gtzan_3f_Win_110250_75/fold2/blues/406_18.wav
blues  ---  gtzan_3f_Win_110250_75/fold1/blues/886_17.wav
classical  ---  gtzan_3f_Win_110250_75/fold2/classical/569_10.wav
country  ---  gtzan_3f_Win_110250_75/fold2/country/435_7.wav
classical  ---  gtzan_3f_Win_110250_75/fold1/classical/800_17.wav
disco  ---  gtzan_3f_Win_110250_75/fold1/disco/925_7.wav
jazz  ---  gtzan_3f_Win_110250_75/fold2/jazz/599_17.wa

classical  ---  gtzan_3f_Win_110250_75/fold2/classical/579_13.wav
rock  ---  gtzan_3f_Win_110250_75/fold2/rock/362_16.wav
hiphop  ---  gtzan_3f_Win_110250_75/fold2/hiphop/505_5.wav
blues  ---  gtzan_3f_Win_110250_75/fold2/blues/408_10.wav
hiphop  ---  gtzan_3f_Win_110250_75/fold1/hiphop/1000_20.wav
blues  ---  gtzan_3f_Win_110250_75/fold1/blues/897_6.wav
jazz  ---  gtzan_3f_Win_110250_75/fold2/jazz/606_12.wav
metal  ---  gtzan_3f_Win_110250_75/fold2/metal/637_1.wav
disco  ---  gtzan_3f_Win_110250_75/fold2/disco/530_15.wav
hiphop  ---  gtzan_3f_Win_110250_75/fold2/hiphop/497_3.wav
hiphop  ---  gtzan_3f_Win_110250_75/fold2/hiphop/508_20.wav
jazz  ---  gtzan_3f_Win_110250_75/fold1/jazz/740_18.wav
rock  ---  gtzan_3f_Win_110250_75/fold2/rock/361_17.wav
pop  ---  gtzan_3f_Win_110250_75/fold2/pop/382_10.wav
rock  ---  gtzan_3f_Win_110250_75/fold1/rock/843_12.wav
disco  ---  gtzan_3f_Win_110250_75/fold1/disco/922_10.wav
classical  ---  gtzan_3f_Win_110250_75/fold1/classical/816_7.wav
country 

metal  ---  gtzan_3f_Win_110250_75/fold1/metal/672_18.wav
pop  ---  gtzan_3f_Win_110250_75/fold2/pop/386_14.wav
pop  ---  gtzan_3f_Win_110250_75/fold1/pop/728_5.wav
jazz  ---  gtzan_3f_Win_110250_75/fold2/jazz/620_9.wav
pop  ---  gtzan_3f_Win_110250_75/fold2/pop/373_17.wav
hiphop  ---  gtzan_3f_Win_110250_75/fold2/hiphop/525_10.wav
blues  ---  gtzan_3f_Win_110250_75/fold1/blues/892_9.wav
classical  ---  gtzan_3f_Win_110250_75/fold2/classical/563_4.wav
blues  ---  gtzan_3f_Win_110250_75/fold1/blues/894_19.wav
country  ---  gtzan_3f_Win_110250_75/fold1/country/776_15.wav
disco  ---  gtzan_3f_Win_110250_75/fold2/disco/561_3.wav
hiphop  ---  gtzan_3f_Win_110250_75/fold2/hiphop/503_11.wav
classical  ---  gtzan_3f_Win_110250_75/fold1/classical/818_14.wav
classical  ---  gtzan_3f_Win_110250_75/fold1/classical/808_2.wav
jazz  ---  gtzan_3f_Win_110250_75/fold2/jazz/618_18.wav
hiphop  ---  gtzan_3f_Win_110250_75/fold1/hiphop/971_1.wav
blues  ---  gtzan_3f_Win_110250_75/fold1/blues/870_6.wav
rock

blues  ---  gtzan_3f_Win_110250_75/fold2/blues/424_13.wav
pop  ---  gtzan_3f_Win_110250_75/fold2/pop/369_15.wav
classical  ---  gtzan_3f_Win_110250_75/fold2/classical/589_17.wav
hiphop  ---  gtzan_3f_Win_110250_75/fold2/hiphop/525_21.wav
hiphop  ---  gtzan_3f_Win_110250_75/fold2/hiphop/514_2.wav
blues  ---  gtzan_3f_Win_110250_75/fold2/blues/429_10.wav
jazz  ---  gtzan_3f_Win_110250_75/fold1/jazz/734_1.wav
pop  ---  gtzan_3f_Win_110250_75/fold2/pop/383_20.wav
pop  ---  gtzan_3f_Win_110250_75/fold1/pop/698_5.wav
disco  ---  gtzan_3f_Win_110250_75/fold2/disco/560_16.wav
metal  ---  gtzan_3f_Win_110250_75/fold1/metal/669_20.wav
classical  ---  gtzan_3f_Win_110250_75/fold1/classical/804_14.wav
country  ---  gtzan_3f_Win_110250_75/fold2/country/443_3.wav
rock  ---  gtzan_3f_Win_110250_75/fold1/rock/846_3.wav
reggae  ---  gtzan_3f_Win_110250_75/fold2/reggae/479_14.wav
metal  ---  gtzan_3f_Win_110250_75/fold1/metal/692_15.wav
pop  ---  gtzan_3f_Win_110250_75/fold1/pop/712_17.wav
hiphop  ---  

In [117]:
label_train.shape

(14051,)

In [118]:
# Let's read each genre from the filename in our list and take the first four characters of the genre directory


choices = {'blues': 0, 'classical': 1, 'country': 2, 'disco': 3, 'hiphop': 4, 'jazz': 5,
           'metal': 6, 'pop': 7, 'reggae': 8, 'rock': 9}

# Let's read each genre from the filename in our list and take the first four characters of the genre directory
i = 0 
for file_name in test_filename_list:
    # Take the first four characters of the file
    class_id = file_name[20:].split('/')[2]
    
    print(class_id, ' --- ', file_name)
    # Replace the 4-character string by a number according to "choices"
    label_test[i] = choices.get(class_id, 99)
    i += 1

metal  ---  gtzan_3f_Win_110250_75/fold3/metal/137_3.wav
metal  ---  gtzan_3f_Win_110250_75/fold3/metal/154_11.wav
metal  ---  gtzan_3f_Win_110250_75/fold3/metal/144_5.wav
metal  ---  gtzan_3f_Win_110250_75/fold3/metal/163_12.wav
metal  ---  gtzan_3f_Win_110250_75/fold3/metal/141_4.wav
metal  ---  gtzan_3f_Win_110250_75/fold3/metal/145_18.wav
metal  ---  gtzan_3f_Win_110250_75/fold3/metal/165_19.wav
metal  ---  gtzan_3f_Win_110250_75/fold3/metal/159_21.wav
metal  ---  gtzan_3f_Win_110250_75/fold3/metal/136_2.wav
metal  ---  gtzan_3f_Win_110250_75/fold3/metal/155_20.wav
metal  ---  gtzan_3f_Win_110250_75/fold3/metal/156_1.wav
metal  ---  gtzan_3f_Win_110250_75/fold3/metal/147_15.wav
metal  ---  gtzan_3f_Win_110250_75/fold3/metal/145_20.wav
metal  ---  gtzan_3f_Win_110250_75/fold3/metal/159_15.wav
metal  ---  gtzan_3f_Win_110250_75/fold3/metal/140_2.wav
metal  ---  gtzan_3f_Win_110250_75/fold3/metal/149_20.wav
metal  ---  gtzan_3f_Win_110250_75/fold3/metal/139_10.wav
metal  ---  gtzan_3f

reggae  ---  gtzan_3f_Win_110250_75/fold3/reggae/51_13.wav
reggae  ---  gtzan_3f_Win_110250_75/fold3/reggae/39_7.wav
reggae  ---  gtzan_3f_Win_110250_75/fold3/reggae/54_3.wav
reggae  ---  gtzan_3f_Win_110250_75/fold3/reggae/57_15.wav
reggae  ---  gtzan_3f_Win_110250_75/fold3/reggae/55_16.wav
reggae  ---  gtzan_3f_Win_110250_75/fold3/reggae/39_15.wav
reggae  ---  gtzan_3f_Win_110250_75/fold3/reggae/43_10.wav
reggae  ---  gtzan_3f_Win_110250_75/fold3/reggae/47_4.wav
reggae  ---  gtzan_3f_Win_110250_75/fold3/reggae/41_14.wav
reggae  ---  gtzan_3f_Win_110250_75/fold3/reggae/46_4.wav
reggae  ---  gtzan_3f_Win_110250_75/fold3/reggae/34_6.wav
reggae  ---  gtzan_3f_Win_110250_75/fold3/reggae/53_16.wav
reggae  ---  gtzan_3f_Win_110250_75/fold3/reggae/62_5.wav
reggae  ---  gtzan_3f_Win_110250_75/fold3/reggae/42_16.wav
reggae  ---  gtzan_3f_Win_110250_75/fold3/reggae/66_6.wav
reggae  ---  gtzan_3f_Win_110250_75/fold3/reggae/54_2.wav
reggae  ---  gtzan_3f_Win_110250_75/fold3/reggae/44_11.wav
regga

jazz  ---  gtzan_3f_Win_110250_75/fold3/jazz/79_4.wav
jazz  ---  gtzan_3f_Win_110250_75/fold3/jazz/69_15.wav
jazz  ---  gtzan_3f_Win_110250_75/fold3/jazz/92_17.wav
jazz  ---  gtzan_3f_Win_110250_75/fold3/jazz/95_13.wav
jazz  ---  gtzan_3f_Win_110250_75/fold3/jazz/99_19.wav
jazz  ---  gtzan_3f_Win_110250_75/fold3/jazz/89_8.wav
jazz  ---  gtzan_3f_Win_110250_75/fold3/jazz/68_13.wav
jazz  ---  gtzan_3f_Win_110250_75/fold3/jazz/68_12.wav
jazz  ---  gtzan_3f_Win_110250_75/fold3/jazz/90_21.wav
jazz  ---  gtzan_3f_Win_110250_75/fold3/jazz/76_2.wav
jazz  ---  gtzan_3f_Win_110250_75/fold3/jazz/76_9.wav
jazz  ---  gtzan_3f_Win_110250_75/fold3/jazz/72_10.wav
jazz  ---  gtzan_3f_Win_110250_75/fold3/jazz/73_10.wav
jazz  ---  gtzan_3f_Win_110250_75/fold3/jazz/92_4.wav
jazz  ---  gtzan_3f_Win_110250_75/fold3/jazz/71_5.wav
jazz  ---  gtzan_3f_Win_110250_75/fold3/jazz/69_11.wav
jazz  ---  gtzan_3f_Win_110250_75/fold3/jazz/77_6.wav
jazz  ---  gtzan_3f_Win_110250_75/fold3/jazz/98_21.wav
jazz  ---  gtzan_

disco  ---  gtzan_3f_Win_110250_75/fold3/disco/291_15.wav
disco  ---  gtzan_3f_Win_110250_75/fold3/disco/290_10.wav
disco  ---  gtzan_3f_Win_110250_75/fold3/disco/286_18.wav
disco  ---  gtzan_3f_Win_110250_75/fold3/disco/284_13.wav
disco  ---  gtzan_3f_Win_110250_75/fold3/disco/270_11.wav
disco  ---  gtzan_3f_Win_110250_75/fold3/disco/276_1.wav
disco  ---  gtzan_3f_Win_110250_75/fold3/disco/280_9.wav
disco  ---  gtzan_3f_Win_110250_75/fold3/disco/289_9.wav
disco  ---  gtzan_3f_Win_110250_75/fold3/disco/276_18.wav
disco  ---  gtzan_3f_Win_110250_75/fold3/disco/289_16.wav
disco  ---  gtzan_3f_Win_110250_75/fold3/disco/278_15.wav
disco  ---  gtzan_3f_Win_110250_75/fold3/disco/296_13.wav
disco  ---  gtzan_3f_Win_110250_75/fold3/disco/285_20.wav
disco  ---  gtzan_3f_Win_110250_75/fold3/disco/274_16.wav
disco  ---  gtzan_3f_Win_110250_75/fold3/disco/271_16.wav
disco  ---  gtzan_3f_Win_110250_75/fold3/disco/278_16.wav
disco  ---  gtzan_3f_Win_110250_75/fold3/disco/281_10.wav
disco  ---  gtzan

pop  ---  gtzan_3f_Win_110250_75/fold3/pop/193_7.wav
pop  ---  gtzan_3f_Win_110250_75/fold3/pop/184_17.wav
pop  ---  gtzan_3f_Win_110250_75/fold3/pop/188_21.wav
pop  ---  gtzan_3f_Win_110250_75/fold3/pop/198_1.wav
pop  ---  gtzan_3f_Win_110250_75/fold3/pop/194_12.wav
pop  ---  gtzan_3f_Win_110250_75/fold3/pop/169_14.wav
pop  ---  gtzan_3f_Win_110250_75/fold3/pop/191_8.wav
pop  ---  gtzan_3f_Win_110250_75/fold3/pop/189_1.wav
pop  ---  gtzan_3f_Win_110250_75/fold3/pop/182_19.wav
pop  ---  gtzan_3f_Win_110250_75/fold3/pop/185_5.wav
pop  ---  gtzan_3f_Win_110250_75/fold3/pop/190_15.wav
pop  ---  gtzan_3f_Win_110250_75/fold3/pop/189_10.wav
pop  ---  gtzan_3f_Win_110250_75/fold3/pop/180_18.wav
pop  ---  gtzan_3f_Win_110250_75/fold3/pop/176_10.wav
pop  ---  gtzan_3f_Win_110250_75/fold3/pop/179_1.wav
pop  ---  gtzan_3f_Win_110250_75/fold3/pop/197_4.wav
pop  ---  gtzan_3f_Win_110250_75/fold3/pop/193_9.wav
hiphop  ---  gtzan_3f_Win_110250_75/fold3/hiphop/19_8.wav
hiphop  ---  gtzan_3f_Win_110250

classical  ---  gtzan_3f_Win_110250_75/fold3/classical/121_5.wav
classical  ---  gtzan_3f_Win_110250_75/fold3/classical/109_5.wav
classical  ---  gtzan_3f_Win_110250_75/fold3/classical/117_13.wav
classical  ---  gtzan_3f_Win_110250_75/fold3/classical/129_9.wav
classical  ---  gtzan_3f_Win_110250_75/fold3/classical/120_7.wav
classical  ---  gtzan_3f_Win_110250_75/fold3/classical/126_1.wav
classical  ---  gtzan_3f_Win_110250_75/fold3/classical/128_15.wav
classical  ---  gtzan_3f_Win_110250_75/fold3/classical/125_5.wav
classical  ---  gtzan_3f_Win_110250_75/fold3/classical/123_20.wav
classical  ---  gtzan_3f_Win_110250_75/fold3/classical/116_11.wav
classical  ---  gtzan_3f_Win_110250_75/fold3/classical/125_4.wav
classical  ---  gtzan_3f_Win_110250_75/fold3/classical/119_2.wav
classical  ---  gtzan_3f_Win_110250_75/fold3/classical/114_20.wav
classical  ---  gtzan_3f_Win_110250_75/fold3/classical/113_2.wav
classical  ---  gtzan_3f_Win_110250_75/fold3/classical/105_11.wav
classical  ---  gtz

blues  ---  gtzan_3f_Win_110250_75/fold3/blues/226_8.wav
blues  ---  gtzan_3f_Win_110250_75/fold3/blues/218_15.wav
blues  ---  gtzan_3f_Win_110250_75/fold3/blues/230_8.wav
blues  ---  gtzan_3f_Win_110250_75/fold3/blues/222_7.wav
blues  ---  gtzan_3f_Win_110250_75/fold3/blues/219_9.wav
blues  ---  gtzan_3f_Win_110250_75/fold3/blues/211_3.wav
blues  ---  gtzan_3f_Win_110250_75/fold3/blues/215_13.wav
blues  ---  gtzan_3f_Win_110250_75/fold3/blues/207_19.wav
blues  ---  gtzan_3f_Win_110250_75/fold3/blues/215_10.wav
blues  ---  gtzan_3f_Win_110250_75/fold3/blues/219_17.wav
blues  ---  gtzan_3f_Win_110250_75/fold3/blues/212_18.wav
blues  ---  gtzan_3f_Win_110250_75/fold3/blues/206_1.wav
blues  ---  gtzan_3f_Win_110250_75/fold3/blues/208_11.wav
blues  ---  gtzan_3f_Win_110250_75/fold3/blues/226_13.wav
blues  ---  gtzan_3f_Win_110250_75/fold3/blues/205_21.wav
blues  ---  gtzan_3f_Win_110250_75/fold3/blues/207_11.wav
blues  ---  gtzan_3f_Win_110250_75/fold3/blues/211_4.wav
blues  ---  gtzan_3f_

country  ---  gtzan_3f_Win_110250_75/fold3/country/238_19.wav
country  ---  gtzan_3f_Win_110250_75/fold3/country/237_13.wav
country  ---  gtzan_3f_Win_110250_75/fold3/country/254_6.wav
country  ---  gtzan_3f_Win_110250_75/fold3/country/257_10.wav
country  ---  gtzan_3f_Win_110250_75/fold3/country/256_8.wav
country  ---  gtzan_3f_Win_110250_75/fold3/country/262_5.wav
country  ---  gtzan_3f_Win_110250_75/fold3/country/240_20.wav
country  ---  gtzan_3f_Win_110250_75/fold3/country/241_8.wav
country  ---  gtzan_3f_Win_110250_75/fold3/country/242_9.wav
country  ---  gtzan_3f_Win_110250_75/fold3/country/247_16.wav
country  ---  gtzan_3f_Win_110250_75/fold3/country/264_13.wav
country  ---  gtzan_3f_Win_110250_75/fold3/country/243_10.wav
country  ---  gtzan_3f_Win_110250_75/fold3/country/257_20.wav
country  ---  gtzan_3f_Win_110250_75/fold3/country/232_3.wav
country  ---  gtzan_3f_Win_110250_75/fold3/country/249_4.wav
country  ---  gtzan_3f_Win_110250_75/fold3/country/253_20.wav
country  ---  g

In [119]:
label_test.shape

(6929,)

In [120]:
#Binary class metrics
from keras.utils import np_utils, to_categorical

Y_train = to_categorical(label_train, num_classes = nb_classes)
label_train = None
gc.collect()
Y_train.shape

(14051, 10)

In [121]:
#Binary class metrics
from keras.utils import np_utils, to_categorical

Y_test = to_categorical( label_test, num_classes = nb_classes)
label_test = None
gc.collect()
Y_test.shape

(6929, 10)

In [122]:
Y_train

array([[0., 0., 0., ..., 1., 0., 0.],
       [0., 0., 0., ..., 0., 0., 1.],
       [0., 0., 0., ..., 0., 0., 0.],
       ...,
       [0., 0., 0., ..., 0., 0., 1.],
       [0., 0., 0., ..., 0., 1., 0.],
       [0., 1., 0., ..., 0., 0., 0.]])

In [123]:
Y_test

array([[0., 0., 0., ..., 0., 0., 0.],
       [0., 0., 0., ..., 0., 0., 0.],
       [0., 0., 0., ..., 0., 0., 0.],
       ...,
       [0., 0., 0., ..., 0., 0., 1.],
       [0., 0., 0., ..., 0., 0., 1.],
       [0., 0., 0., ..., 0., 0., 1.]])

## Save label files to disk (.npy files)

In [124]:
np.save( "folds_stft/2_GTzan_Ys_train_fold"+f_s_folds+"_110250_75_frozen_stft.npy", Y_train)

In [125]:
np.save( "folds_stft/2_GTzan_Ys_test_fold"+o_fold+"_110250_75_frozen_stft.npy", Y_test)

## Keep track of track names and segments

- important to concatenate the audio segments at classification

In [126]:
# Create a big matrix to accomodate tracks_ids and segments
track_list_train = np.ones( (spchnumber_train,), dtype=int )
print( track_list_train.shape )
seg_list_train = np.ones( (spchnumber_train,), dtype=int )
print( seg_list_train.shape )

(14051,)
(14051,)


In [127]:
# Create a big matrix to accomodate tracks_ids and segments
track_list_test = np.ones( (spchnumber_test,), dtype=int )
print( track_list_test.shape )
seg_list_test = np.ones( (spchnumber_test,), dtype=int )
print( seg_list_test.shape )

(6929,)
(6929,)


In [128]:
i = 0

for file_name in train_filename_list:
    # Take the first four characters of the file
    track_id = file_name[20:].split('/')[3].split('_')[0]
    seg_id   = file_name[20:].split('_')[-1].split('.')[0]
    track_list_train[i] = track_id
    seg_list_train[i]     = seg_id
    i += 1

In [129]:
i = 0

for file_name in test_filename_list:
    # Take the first four characters of the file
    track_id = file_name[20:].split('/')[3].split('_')[0]
    seg_id   = file_name[20:].split('_')[-1].split('.')[0]
    track_list_test[i]  = track_id
    seg_list_test[i]     = seg_id
    i += 1

In [130]:
seg_id 

'1'

In [131]:
track_id

'303'

In [132]:
train_filename_list = None
test_filename_list  = None
label = None
gc.collect()

0

## Save track list and segment list to disk (.npy files)

In [133]:
np.save( "folds_stft/2_GTzan_ts_train_fold"+f_s_folds+"_110250_75_frozen_stft.npy", track_list_train)

In [134]:
np.save( "folds_stft/2_GTzan_ts_test_fold"+o_fold+"_110250_75_frozen_stft.npy", track_list_test)

In [135]:
track_list = None
gc.collect()

0

In [136]:
np.save( "folds_stft/2_GTzan_ss_train_fold"+f_s_folds+"_110250_75_frozen_stft.npy", seg_list_train)

In [137]:
np.save( "folds_stft/2_GTzan_ss_test_fold"+o_fold+"_110250_75_frozen_stft.npy", seg_list_test)

In [138]:
seg_list = None
gc.collect()

0